In [1]:
from datasets import load_dataset
import pandas as pd
import os
import re
import string
from tqdm import tqdm

In [2]:
from nltk.tokenize import word_tokenize
import nltk


In [3]:
nltk.data.path.append(os.path.abspath('nltk_data'))

In [4]:

# nltk.download('stopwords' , download_dir='nltk_data')
# nltk.download('wordnet' , download_dir='nltk_data')
nltk.download('punkt_tab', download_dir='nltk_data')

[nltk_data] Downloading package punkt_tab to nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

---


In [5]:
main_path = os.path.abspath('../../Datasets/CSV/HasilPreprocessingPutusan.csv')

In [6]:
main_df = pd.read_csv(main_path)
main_df

Unnamed: 0                             nama_file  \
0             1  0562ade93fdb9218eb4c383fda670b99.txt   
1             3  0bc2ad597f9aa2bd8758f1fac16c479b.txt   
2             6  10e1c3597cfeb112b3b957609972b996.txt   
3             8  12685851e8dfed8cbd76ae6f4854e65d.txt   
4            10  178fbc570d83459cf7048788fc69d7b7.txt   
..          ...                                   ...   
340         412  zaf016a9bde944e4b157313435313133.txt   
341         413  zaf01fed3c738ab2bf28303934373033.txt   
342         414  zaf0201f53a267a8beb0313534353336.txt   
343         415  zaf0201f55c473d284d9313534353430.txt   
344         416  zaf0240d97731d469c13313534383434.txt   

               Nomor Putusan                     Nama Terdakwa 1  \
0    161/pid. b/2020/pn bkl          samuri alias mori bin samin   
1    201/pid. b/2019/pn bkl                       muis bin sujai   
2    162/pid. b/2019/pn bkl                 masir bin tamin alm.   
3    192/pid. b/2019/pn bkl           h.  abd aziz al.  h.  aziz   
4      9/pid. b/2019/pn bkl         h.  muzammil bin mattingwar.   
..                       ...                                 ...   
340   31/pid. b/2025/pn bkl    nur holis alias kholis bin selket   
341   47/pid. b/2025/pn bkl   andika dwi tripratama bin suratman   
342   60/pid. b/2020/pn bkl            mat bakri bin jaman (alm)   
343   77/pid. b/2025/pn bkl              muhamad arip bin mahpud   
344   60/pid. b/2025/pn bkl                    sujai bin marikan   

    Nama Terdakwa 2 Nama Terdakwa 3  \
0               NaN             NaN   
1               NaN             NaN   
2               NaN             NaN   
3               NaN             NaN   
4               NaN             NaN   
..              ...             ...   
340             NaN             NaN   
341             NaN             NaN   
342             NaN             NaN   
343             NaN             NaN   
344             NaN             NaN   

                                       Tuntutan Pidana  \
0                                            perjudian   
1    “pencurian dengan kekerasan atau ancaman keker...   
2                          pencurian dengan pemberatan   
3                         “pencurian dengan kekerasan”   
4                                           “penipuan”   
..                                                 ...   
340        “penggelapan” melanggar pasal 372 kuhpidana   
341  “percobaan pencurian ” melanggar pasal 362 kuh...   
342  “pencurian dengan pemberatan ” melanggar pasal...   
343  “ pencurian dengan pemberatan ” melanggar pasa...   
344  “melakukan perbuatan penganiayaan atau dengan ...   

                            Tuntutan KUHP  \
0            pasal 303 ayat (1) ke-2 kuhp   
1       pasal 365 ayat (2) ke-1,ke-2 kuhp   
2            pasal 363 ayat (1) ke-3 kuhp   
3    pasal 365 ayat (2) ke-1 kitab undang   
4                          pasal 372 kuhp   
..                                    ...   
340                pasal 372 kitab undang   
341                        pasal 362 kuhp   
342          pasal 363 ayat (1) ke-4 kuhp   
343          pasal 363 ayat (1) ke-4 kuhp   
344      pasal 351 ayat (1) kitab  undang   

                             Tuntutan Hukuman  \
0                             5 (lima) bulan;   
1                             5 (lima) tahun;   
2                         9 (sembilan) bulan;   
3                            4 (empat) tahun;   
4                             1 (satu) tahun;   
..                                        ...   
340            1 (satu) tahun 6 (enam) bulan;   
341        1 (satu) tahun dan 3 (tiga) bulan;   
342                            2 (dua) tahun;   
343                            2 (dua) tahun;   
344  1 (satu) tahun dan 9 (se mbilan) bulan ;   

                                        Putusan Pidana  \
0                                            perjudian   
1                 “pencurian dengan ancaman kekerasan”   
2               “pencurian dalam 

In [7]:
main_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 345 entries, 0 to 344
Data columns (total 18 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   Unnamed: 0        345 non-null    int64 
 1   nama_file         345 non-null    object
 2   Nomor Putusan     345 non-null    object
 3   Nama Terdakwa 1   345 non-null    object
 4   Nama Terdakwa 2   51 non-null     object
 5   Nama Terdakwa 3   12 non-null     object
 6   Tuntutan Pidana   316 non-null    object
 7   Tuntutan KUHP     345 non-null    object
 8   Tuntutan Hukuman  345 non-null    object
 9   Putusan Pidana    312 non-null    object
 10  Putusan Hukuman   345 non-null    object
 11  Tanggal Putusan   343 non-null    object
 12  Hakim Ketua       345 non-null    object
 13  Hakim Anggota 1   324 non-null    object
 14  Hakim Anggota 2   211 non-null    object
 15  Panitera          324 non-null    object
 16  Penuntut Umum     345 non-null    object
 17  content         

In [ ]:
text_columns = main_df.select_dtypes(include='object').columns

---


In [8]:
def normalize_text(text):
    text = re.sub(r'\bmajelis\b', '', text, flags=re.I)
    text = re.sub(r'\s+', ' ', text)
    text = re.sub(r'\s+/', '/', text) 
    text = re.sub(r'^\s*,', '', text)
    text = re.sub(r'["“”]', '', text)
    text = re.sub(r'[":”]', '', text) 
    return text.strip()

In [9]:
def generate_label(entities):
    label = {}

    
    def update_label(entity_list, label, label_value):
        if isinstance(entity_list, list) and entity_list: 
            if len(entity_list) > 1:
                for ent in entity_list:
                    # Normalisasi entitas sebelum ditambahkan ke label
                    normalized_ent = normalize_text(ent)
                    if normalized_ent:
                        label[label_value] = label.get(label_value, []) + [normalized_ent] 
            else:
                # Jika hanya ada satu entitas, normalisasi terlebih dahulu
                normalized_ent = normalize_text(entity_list[0])
                label[label_value] = label.get(label_value, []) + [normalized_ent]
        elif isinstance(entity_list, str) and entity_list.strip():
            # Normalisasi entitas yang berupa string
            normalized_ent = normalize_text(entity_list)
            label[label_value] = label.get(label_value, []) + [normalized_ent]
            
    

    # Melabeli entitas yang ada di 'Penuntut Umum', 'Nama Terdakwa', dll.
    if 'Penuntut Umum' in entities and entities['Penuntut Umum']:
        update_label(entities['Penuntut Umum'], label, "B_PROS")

    for i in range(1, 4): 
        key = f'Nama Terdakwa {i}'
        if key in entities and entities[key]:
            update_label(entities[key], label, "B_DEFN")

    for i in range(1, 3):
        key = f'Hakim Anggota {i}'
        if key in entities and entities[key]:
            update_label(entities[key], label, "B_JUDG")

    if 'Tuntutan Hukuman' in entities and entities['Tuntutan Hukuman']:
        value = entities['Tuntutan Hukuman'].strip()
        if value in label:
            label["B_PENA"] = label.get("B_PENA", []) + [value]
        else:
            update_label(entities['Tuntutan Hukuman'], label, "B_PENA")
        
    if 'Putusan Hukuman' in entities and entities['Putusan Hukuman']:
        value = entities['Putusan Hukuman'].strip()
        if value in label:
            label["B_PUNI"] = label.get("B_PUNI", []) + [value]
        else:
            update_label(entities['Putusan Hukuman'], label, "B_PUNI")   

    if 'Nomor Putusan' in entities:
        update_label(entities['Nomor Putusan'], label, "B_VERN")
    if 'Tanggal Putusan' in entities:
        update_label(entities['Tanggal Putusan'], label, "B_TIMV")
    if 'Hakim Ketua' in entities:
        update_label(entities['Hakim Ketua'], label, "B_JUDP")
    if 'Panitera' in entities:
        update_label(entities['Panitera'], label, "B_REGI")
    if 'Tuntutan Pidana' in entities:
        update_label(entities['Tuntutan Pidana'], label, "B_CRIA")
    if 'Tuntutan KUHP' in entities:
        update_label(entities['Tuntutan KUHP'], label, "B_ARTV")
        
    return label


In [10]:
# label = generate_label(main_df.iloc[3].to_dict())
# label


In [23]:
    
def labeling_token(text, label_dict):
    text = text.lower()  # Tokenize the text
    text = re.sub(r'\b(p\s*u\s*t\s*u\s*s\s*a\s*n)\b', 'putusan', text)
    tokens = text.split()
    print(tokens)# Tokenize the text using whitespace  
    labeled_tokens = ['O'] * len(tokens) 
    find_label = dict()
    for label, entities in label_dict.items():
            if isinstance(entities, list): 
                for entity in entities:
                    words = entity.split()
                    if not words:  # Skip if words is empty
                        continue
                    current_dict = find_label
                    for word in words[:-1]:
                        word = re.sub(r'[.,;":]', '', word)
                        current_dict = current_dict.setdefault(word, {})
                    last_word = re.sub(r'[.,;":]', '', words[-1]) 
                    current_dict[last_word] = {'label': label}
            else:  
                words = entities.split()
                if not words:  # Skip if words is empty
                    continue
                current_dict = find_label
                for word in words[:-1]:
                    word = re.sub(r'[.,;":]', '', word)  
                    current_dict = current_dict.setdefault(word, {})
                last_word = re.sub(r'[.,;":]', '', words[-1])
                current_dict[last_word] = {'label': label}

    temp_idx_token = []  
    find_label_selected = find_label

    for i, token in enumerate(tokens):
        clean_token = re.sub(r'[.,;":]', '', token)
        if clean_token in find_label_selected:
            find_label_selected = find_label_selected[clean_token]
            temp_idx_token.append(i)
            if 'label' in find_label_selected:
                tag = find_label_selected['label']
                for ind in range(len(temp_idx_token)):
                    if ind == 0:
                        labeled_tokens[temp_idx_token[ind]] = tag
                    else:
                        labeled_tokens[temp_idx_token[ind]] = tag.replace('B', 'I')
                temp_idx_token = [] 
                find_label_selected = find_label 
        else:
            temp_idx_token = []
            find_label_selected = find_label 

    return labeled_tokens


In [12]:
main_df['content'][8]

'PUTUSAN\n Nomor 431/Pid. B/2018/PN Bkl DEMI KEADILAN BERDASARKAN KETUHANAN YANG MAHA ESA Pengadilan Negeri Bangkalan, yang memeriksa dan mengadili perkara- perkara pidana dengan acara pemeriksaan biasa, dalam tingkat pertama telah menjatuhkan putusan sebagai berikut, dalam perkara terdakwa :  Nama lengkap : MOCH.  TUKI. \nTempat lahir : Bangkalan . \nUmur/tgl.  lahir : 21 tahun / 01 Juli 1997  Jenis kelamin : Laki-laki . \nKebangsaan : Indonesia . \nTempat tinggal : Dusun Nong Malang, Desa Bunajih, Kecamatan. \nLabang, Kabupaten Bangkalan  Agama : Islam. \nPekerjaan : Petani Pendidikan : SD lulus  Terdakwa ditangkap pada tanggal 10 Oktober 2018 berdasarkan Surat Perintah Penangkapan tanggal 10 Oktober 2018 Nomor : SP. Kap/12/X/RES. 1. 6/ 2018/Sek. Sukolilo ;\nTerdakwa ditahan berdasarkan Surat Perintah Penetapan Penahanan dari :\n1. Penyidik, tanggal 11 Oktober 2018 Nomor : SPP/218/X/RES. 1. 6/2018/Sek. \nSukolilo, sejak tanggal 11 Oktober 2018 s/d tanggal 30 Oktober 2018 ;\n2. Perpan

In [13]:
testlabel = generate_label(main_df.iloc[89].to_dict())
testlabel

{'B_PROS': ['siti bulkis,s. h. , jaksa'],
 'B_DEFN': ['hendri setiawan'],
 'B_JUDG': ['sugiri wiryandono,s. h. ,m. hum. ,',
  'vilaningrum wibawani, s. h. , m. h. ,'],
 'B_PENA': ['bulan 6 (enam bulan) ;'],
 'B_PUNI': ['bulan 6 (enam bulan) ;'],
 'B_VERN': ['373/pid. b/2017/pn. bkl'],
 'B_TIMV': ['tanggal 21 februari 2018'],
 'B_JUDP': ['h. bawono effendi ,s. h. , m. h. ,'],
 'B_REGI': ['naruddin, s. h. ,sebagai'],
 'B_CRIA': ['penipuan yang dilakukan secara bersama-sama'],
 'B_ARTV': ['pasal 378 kuhp']}

In [24]:
testlabelstokens = labeling_token(main_df.iloc[89]['content'], testlabel)
# labelstokens[:20]

['putusan', 'nomor', '373/pid.', 'b/2017/pn.', 'bkl', '“demi', 'keadilan', 'berdasarkan', 'ketuhanan', 'yang', 'maha', 'esa”', 'pengadilan', 'negeri', 'bangkalan', 'yang', 'mengadili', 'perkara-perkara', 'pidana', 'dengan', 'acara', 'biasa', 'pada', 'peradilan', 'tingkat', 'pertama', 'telah', 'menjatuhkan', 'putusan', 'sebagai', 'berikut', 'dalam', 'perkara', 'atas', 'namaterdakwa:', 'nama', ':hendri', 'setiawan', ';.', 'tempat', 'lahir', ':bangkalan', ';', 'umur/tgl.', 'lahir', ':35', 'tahun', '/', '11', 'pebruari', '1982', ';', 'jenis', 'kelamin', ':laki-laki', ';', 'kebangsaan', ':indonesia', '/', 'suku', 'madura', ';.', 'tempat', 'tinggal', ':jl.', 'sumber', 'sari', 'dalam', 'rt/rw', '002/003', 'ds.', 'banyuajuh,', 'kec.', 'kamal', 'kab.', 'bangkalan', ';', 'agama', ':islam', ';.', 'pekerjaan', ':polri', ';', 'pendidikan', ':sma', ';', 'terdakwa', 'ditahan', 'dalam', 'tahanan', 'rutan', 'berdasarkan', 'penetapan', 'oleh', ':', '-penyidik', 'sejak', 'tanggal', '25', 'oktober', '2017

In [15]:
testlabelstokens[:2000]

['O',
 'O',
 'B_VERN',
 'I_VERN',
 'I_VERN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'B_DEFN',
 'I_DEFN',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O',
 'O

In [16]:
def handleDuplicatePena(sequences):
    countPena = 0

    for sequence in sequences:
        for i, label in enumerate(sequence):
            if label == 'B_PENA': 
                countPena += 1
                if countPena > 1:  
                    sequence[i] = 'B_PUNI' 
            elif label == 'I_PENA':  
                if countPena > 1: 
                    sequence[i] = 'I_PUNI' 

    return sequences


In [17]:
def countLabel(doc_idx, data, label_ori):
    result = {}
    label_found = set()
    label_list = set(['B_ARTV', 'B_DEFN', 'B_PROS', 'B_CRIA', 'B_JUDP', 'B_VERN', 'B_PUNI', 'B_JUDG', 'B_REGI', 'B_TIMV', 'B_PENA'])
    for i, row in data.iterrows():
      for t, l in zip(row["word"], row["tag"]):
        if l != 'O' and l.replace('I_', 'B_') not in label_found:
          label_found.add(l.replace('I_', 'B_'))

    label_missing = label_list - label_found
    result[f"Dokumen Ke-{doc_idx}"] = (len(label_found), len(label_ori), label_missing)
    return result



def anotasi(data):
    content_results = pd.DataFrame(columns=["doc", "word", "tag"])
    count_label = {}
    labels = []

    for doc_idx, (_, row) in tqdm(enumerate(data.iterrows()), total=len(data), desc="Annotating"):
        temp_results = {"doc": [], "word": [], "tag": []}

        label = generate_label(row)
        labels.append(label)
        content = row["content"]
        labeled_tokens = labeling_token(content, label)

        doc_str = f"doc:{doc_idx+1}"
        temp_results["doc"].append(doc_str)
        temp_results["word"].append(content.split())
        temp_results["tag"].append(labeled_tokens)
        temp_results['tag'] = handleDuplicatePena(temp_results['tag'])

        temp_data = pd.DataFrame(temp_results)
        count_label.update(countLabel(f"{doc_idx}", temp_data, label))
        content_results = pd.concat([content_results, temp_data], ignore_index=True)

    return content_results, count_label, labels


In [18]:


def accuracy(result):
  sum_label = 0
  label_in = 0
  for key, value in result.items():
    print(f"{key} => Data Terlebel : {value[0]} ; Total Label : {value[1]} ; Label Hilang : {value[2]}")
    sum_label+= value[1]
    label_in += value[0]

  return f"Accuracy : {label_in/sum_label * 100}"

In [19]:
anot_df, count_label, labels = anotasi(main_df)


Annotating: 100%|██████████| 345/345 [00:03<00:00, 109.70it/s]


In [20]:
anot_df

doc                                               word  \
0      doc:1  [PUTUSAN, Nomor, 161/Pid., B/2020/PN, Bkl, DEM...   
1      doc:2  [PUTUSAN, Nomor, 201/Pid., B/2019/PN, Bkl, DEM...   
2      doc:3  [PUTUSAN, Nomor, 162/Pid., B/2019/PN, Bkl, DEM...   
3      doc:4  [PUTUSAN, Nomor, 192/Pid., B/2019/PN, Bkl, DEM...   
4      doc:5  [PUTUSAN, Nomor, 9/Pid., B/2019/PN, Bkl, DEMI,...   
..       ...                                                ...   
340  doc:341  [PUTUSAN, Nomor, 31/Pid., B/2025/PN, Bkl, DEMI...   
341  doc:342  [PUTUSAN, Nomor, 47/Pid., B/2025/PN, Bkl, DEMI...   
342  doc:343  [PUTUSAN, Nomor, 76/Pid., B/2025/PN, Bkl, DEMI...   
343  doc:344  [PUTUSAN, Nomor, 77/Pid., B/2025/PN, Bkl, DEMI...   
344  doc:345  [Nomor, 60/Pid., B/2025/PN, Bkl, DEMI, KEADILA...   

                                                   tag  
0    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
1    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
2    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
3    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
4    [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
..                                                 ...  
340  [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
341  [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
342  [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, ...  
343  [O, O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, ...  
344  [O, B_VERN, I_VERN, I_VERN, O, O, O, O, O, O, ...  

[345 rows x 3 columns]

In [21]:
accuracy(count_label)

Dokumen Ke-0 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-1 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-2 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-3 => Data Terlebel : 9 ; Total Label : 11 ; Label Hilang : {'B_ARTV', 'B_PENA'}
Dokumen Ke-4 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-5 => Data Terlebel : 9 ; Total Label : 11 ; Label Hilang : {'B_VERN', 'B_PENA'}
Dokumen Ke-6 => Data Terlebel : 9 ; Total Label : 11 ; Label Hilang : {'B_CRIA', 'B_PENA'}
Dokumen Ke-7 => Data Terlebel : 9 ; Total Label : 11 ; Label Hilang : {'B_PENA', 'B_DEFN'}
Dokumen Ke-8 => Data Terlebel : 10 ; Total Label : 11 ; Label Hilang : {'B_PENA'}
Dokumen Ke-9 => Data Terlebel : 9 ; Total Label : 11 ; Label Hilang : {'B_CRIA', 'B_PENA'}
Dokumen Ke-10 => Data Terlebel : 9 ; Total Label : 11 ; Label Hilang : {'B_TIMV', 'B_PENA'}
Dokumen Ke-11 => Data Terlebel : 9 ; Total 

'Accuracy : 80.92423428264374'

In [25]:
def split_token(dataset):
    dataset_copy = dataset.copy()  # Salin dataset agar tidak memodifikasi data asli
    for i, row in tqdm(dataset_copy.iterrows(), total=len(dataset_copy), desc="Processing rows"):
        for index, (text, tag) in enumerate(zip(row["word"], row["tag"])):
            if tag != "O":
                token = re.findall(r'[^\/,\.():;]+|[\/\.,():;]', text)
                add_label = []
                for i in range(len(token)):
                    if 'B' in tag and not add_label:
                        add_label.append(tag)
                    else:
                        if token[i] != ';':
                            add_label.append(tag.replace('B', 'I'))
                        else:
                            add_label.append('O')

                del row["word"][index]
                del row["tag"][index]
                row["word"][index:index] = token
                row["tag"][index:index] = add_label
            else:
                token = re.findall(r'[^\/,\.():;]+|[\/\.,():;]', text)
                add_label = ['O'] * len(token)  # Set label 'O' untuk semua token

                del row["word"][index]
                del row["tag"][index]
                row["word"][index:index] = token
                row["tag"][index:index] = add_label
    return dataset_copy


In [26]:
tokenize_df = split_token(anot_df)
# 

Processing rows: 100%|██████████| 345/345 [00:23<00:00, 14.63it/s]


In [29]:
filtered_rows = tokenize_df.loc[tokenize_df['doc'] == f'doc:{4}']
text_example = []
for sentence_tokens in filtered_rows['word']:
    text_example.extend(sentence_tokens)
label_example = []
for sentence_tokens in filtered_rows['tag']:
    label_example.extend(sentence_tokens)
print(text_example)
print(label_example)

['PUTUSAN', 'Nomor', '192', '/', 'Pid', '.', 'B', '/', '2019', '/', 'PN', 'Bkl', 'DEMI', 'KEADILAN', 'BERDASARKAN', 'KETUHANAN', 'YANG', 'MAHA', 'ESA', 'Pengadilan', 'Negeri', 'Bangkalan', 'yang', 'mengadili', 'perkara', 'pidana', 'dengan', 'acara', 'pemeriksaan', 'biasa', 'dalam', 'tingkat', 'pertama', 'menjatuhkan', 'putusan', 'sebagai', 'berikut', 'dalam', 'perkara', 'Terdakwa', ':', 'Nama', 'lengkap', ':', 'H', '.', 'Abd', 'Aziz', 'Al', '.', 'H', '.', 'Aziz', ';', '.', 'Tempat', 'lahir', ':', 'Bangkalan', ';', '.', 'Umur', '/', 'tanggal', 'lahir', ':', '44', 'Tahun', '/', '5', 'Mei', '1975', ';', '.', 'Jenis', 'kelamin', ':', 'Laki-laki', ';', '.', 'Kebangsaan', ':', 'Indonesia', ';', '.', 'Tempat', 'tinggal', ':', 'Dusun', 'Duur', 'Desa', 'Langkap', ',', 'Kecamatan', 'Burneh', ',', '.', 'Kabupaten', 'Bangkalan', ';', 'Agama', ':', 'Islam', ';', '.', 'Pekerjaan', ':', 'Tidak', 'bekerja', ';', 'Dalam', 'perkara', 'ini', ',', 'Terdakwa', 'ditangkap', 'oleh', 'Penyidik', 'dalam', 'per

In [30]:
for token, label in zip(text_example, label_example):
  if label != 'O' or token == ' ':
    print(f"Token Word : {token} => {label}")

Token Word : 192 => B_VERN
Token Word : / => I_VERN
Token Word : Pid => I_VERN
Token Word : . => I_VERN
Token Word : B => I_VERN
Token Word : / => I_VERN
Token Word : 2019 => I_VERN
Token Word : / => I_VERN
Token Word : PN => I_VERN
Token Word : Bkl => I_VERN
Token Word : H => B_DEFN
Token Word : . => I_DEFN
Token Word : Abd => I_DEFN
Token Word : Aziz => I_DEFN
Token Word : Al => I_DEFN
Token Word : . => I_DEFN
Token Word : H => I_DEFN
Token Word : . => I_DEFN
Token Word : Aziz => I_DEFN
Token Word : 192 => B_VERN
Token Word : / => I_VERN
Token Word : Pid => I_VERN
Token Word : . => I_VERN
Token Word : B => I_VERN
Token Word : / => I_VERN
Token Word : 2019 => I_VERN
Token Word : / => I_VERN
Token Word : PN => I_VERN
Token Word : Bkl => I_VERN
Token Word : 192 => B_VERN
Token Word : / => I_VERN
Token Word : Pid => I_VERN
Token Word : . => I_VERN
Token Word : B => I_VERN
Token Word : / => I_VERN
Token Word : 2019 => I_VERN
Token Word : / => I_VERN
Token Word : PN => I_VERN
Token Word : 

In [31]:
import pandas as pd

new_rows = []
fragment_id = 1

for _, row in tokenize_df.iterrows():
    fragments, labels, fragment, label = [], [], [], []

    for word, label_word in zip(row['word'], row['tag']):
        if word != ';':
            fragment.append(word)
            label.append(label_word)
        else:
            if fragment:
                fragments.append(fragment)
                labels.append(label)
            fragment, label = [], []

    if fragment:
        fragments.append(fragment)
        labels.append(label)

    for i, (fragment, label) in enumerate(zip(fragments, labels), start=1):
        new_rows.append({'word': fragment, 'tag': label, 'doc': row['doc'], 'fragment': f'fragment:{fragment_id}'})
        fragment_id += 1

df_perfrag = pd.DataFrame(new_rows)

df_pertoken = pd.DataFrame(
    [{'word': token, 'tag': label, 'doc': row['doc'], 'fragment': row['fragment']}
     for _, row in df_perfrag.iterrows()
     for token, label in zip(row['word'], row['tag'])]
)

df_pertoken = df_pertoken.rename(columns={'word': 'token'}).reindex(columns=['doc','fragment', 'token', 'tag'])
df_pertoken

doc        fragment    token     tag
0          doc:1      fragment:1  PUTUSAN       O
1          doc:1      fragment:1    Nomor       O
2          doc:1      fragment:1      161  B_VERN
3          doc:1      fragment:1        /  I_VERN
4          doc:1      fragment:1      Pid  I_VERN
...          ...             ...      ...     ...
2537884  doc:345  fragment:50030        ,       O
2537885  doc:345  fragment:50030        S       O
2537886  doc:345  fragment:50030        .       O
2537887  doc:345  fragment:50030        H       O
2537888  doc:345  fragment:50030        .       O

[2537889 rows x 4 columns]

In [34]:
df_pertoken.to_csv('../../Datasets/ANOTASI/HasilAnotasiPutusan.csv', index=False, )